# Ejemplo para el cálculo de costes de reparacion en el grado de desarrollo de proyecto de inversión: Parte 2 - Verificación simultánea de todos los modos de fallo principales a lo largo de la vida útil

Este ejemplo continuará a partir de los datos de entrada guardados al final del apartado [Parte 1 - Lectura de los datos de entrada.](co_costes_reparacion_01_pi.ipynb)

De acuerdo con el Articulado de la ROM 1.1, la verificación de la fase de conservación - reparación del dique se realiza en cada uno de los estados de que componen la vida útil. Se debe verificar de forma simultánea la seguridad frente a la totalidad de los modos de fallo principales. El esquema seguido para la verificación se muestran en el  documento del Manual de la ROM 1.1. La verificación en este alcance se realiza un número elevado de veces, una por cada serie climática simulada y propagada al emplazamiento. En este ejemplo se muestra la verificación de una de las series climáticas simuladas. Del mismo modo se realizaría para el resto de series climáticas.

## Importación de paquetes de IPython

In [9]:
# hidden
import environment as env
env.initialize()

In [10]:
# Python 2/3 setup 
from __future__ import (absolute_import, division, print_function, unicode_literals)
# from builtins import *

In [11]:
# Juypyter setup

%matplotlib inline
import os
import sys
import pickle
import ast
import pandas as pd
env.pandas_setup()
from IPython.display import HTML

In [12]:
sim_path = os.path.join(env.modules_path ,'AP_PI_reparacion_est_conservadora', 'datos', 'sim_01')

if sim_path not in sys.path:
    sys.path.append(sim_path)

## Carga de variables del apartado anterior

In [13]:
# Getting back the objects:
dir_data = os.path.join(env.data_path, 'reparacion', 'proyecto_inversion', 'var_co_costes_reparacion_01_pi.pkl')

with open(dir_data) as f:  # Python 3: open(..., 'rb')
    ruta_de, ruta_ds, alcance, estrategia, de_planta, de_esquema_division_dique, de_diagrama_modos, clima_tramos, cadencia, de_tipo_verificacion, de_verificacion_tramos, peralte, de_reparacion_necesarios, de_reparacion_disponibles, de_arbol_fallo = pickle.load(f)

## Importación de paquetes para el ejemplo

In [14]:
import logging

from reparacion.calculos import calculo_final_simulacion
from reparacion.calculos import inicializacion_matrices_grado_averia

from reparacion.calculos import estado_de_mar_tramo
from reparacion.calculos import actuliza_nivel_de_averia
from reparacion.clasificacion_main_ciclos import clasificacion_main_ciclos

from tqdm import tqdm

### RUTA PARA LA CREACIÓN DEL FICHERO DE LOG

In [15]:
direct = os.path.join(ruta_ds, 'debug_info.log')
logging.basicConfig(filename=direct, level=logging.INFO)

## Verificación de la estrategia de reparación a lo largo de la vida útil

In [16]:
# Calculo de la hora final de simulacion
h_fin_sim = calculo_final_simulacion(de_planta, clima_tramos, cadencia)

# Inicializar las matrices de grado de averia para el dique, tramos, subsistemas y modos de fallo
(ia_dique, ia_tramos, ia_subsistemas, ia_modos_fallo, averia_estado, averia_acum_estado,
 estado_modos_fallo, subsistemas, tramos, modos_fallo, estado_reparacion_modos,
 origen_maquinaria_reparacion_estado, origen_materiales_reparacion_estado,
 origen_mano_obra_reparacion_estado,
 datos_salida,
 datos_salida_prob_ini_averia) = inicializacion_matrices_grado_averia(de_esquema_division_dique, h_fin_sim)

 # Inicializacion de las matrices de materiales de reparacion que quedan disponibles en puerto y matrices de si
 # los elementos de reparacion se toman del puerto o se encargan para cada estado

# Recorrido por los estados de la vida util
for h in tqdm(range(1, h_fin_sim)):

    # Recorrido por los modos de fallo principales de cada subsistema de cada tramo
    for mst in de_esquema_division_dique.iterrows():
        # Obtencion del tramo, subsistema y modo de fallo
        mst = mst[1]
        tr = mst['tramo']
        ss = mst['subsistema']
        mf = mst['modo_fallo']
        # Se obtienen los datos del estado de mar para el tramo
        (hs, tp, u10, z, p90) = estado_de_mar_tramo(clima_tramos, tr, h)

        logging.info('Estado de mar. Hs: ' + str(hs))

#            if mf == 'MF_4':
#                print mf

        # Actualizacion del nivel de averia acumulado hasta este estado
        (averia_estado, averia_acum_estado) = actuliza_nivel_de_averia(averia_estado, averia_acum_estado, tr, ss,
                                                                       mf, h)
        # En primer lugar se comprueba si el estado corresponde a ciclo de solicitacion o no
        [datos_salida, averia_acum_estado, averia_estado, estado_modos_fallo, origen_maquinaria_reparacion_estado,
         origen_materiales_reparacion_estado, origen_mano_obra_reparacion_estado] = \
               clasificacion_main_ciclos(hs, tp, u10, z, p90, h, tr, ss, mf, averia_acum_estado, averia_estado, de_reparacion_necesarios,
                   de_reparacion_disponibles, estado_reparacion_modos, origen_maquinaria_reparacion_estado,
                   origen_materiales_reparacion_estado, origen_mano_obra_reparacion_estado, alcance,
                   estrategia, datos_salida, estado_modos_fallo, ia_modos_fallo, cadencia, de_verificacion_tramos,
                   peralte, de_esquema_division_dique, de_arbol_fallo, de_tipo_verificacion, clima_tramos, de_diagrama_modos,
                   ia_tramos, ia_subsistemas, subsistemas, ia_dique, tramos, datos_salida_prob_ini_averia)


    # Al final de cada iteracion actualizo los inicios de averia de los susbsistemas y tramos si alguno de los
    # elementos que lo conforman se encuentra en inicio de averia y si todos estan sin averia, el sussitema o
    # tramo deja de tener inicio de averia

        # Inicio de averia en subsistemas
        for s in subsistemas:
            if all(ia_modos_fallo.loc[(slice(None), s), 'ini_averia'] == 0):
                ia_subsistemas.loc[(slice(None), s), 'ini_averia'] = 0
            elif any(ia_modos_fallo.loc[(slice(None), s), 'ini_averia'] == 1):
                ia_subsistemas.loc[(slice(None), s), 'ini_averia'] = 1

        # Inicio de averia en tramos
        for t in tramos:
            if all(ia_subsistemas.loc[t, 'ini_averia'] == 0):
                ia_tramos.loc[t, 'ini_averia'] = 0
            elif any(ia_subsistemas.loc[t, 'ini_averia'] == 1):
                ia_tramos.loc[t, 'ini_averia'] = 1

    # Al final de cada iteracion se comprueba si el dique ha fallado, en caso afirmativo se corta la simulacion
    if ia_dique.ix[0, 'dest_total'] == 1:
        logging.info('Estado: ' + str(h) + ' Tramo: ' + str(tr) + ' Subsistema: ' + str(
            ss) + ' Modo_fallo: ' + str(mf) + ' El dique sufre destruccion total')
        break

  0%|          | 0/14599 [00:00<?, ?it/s]C:\Users\GDFA-JUAN\Anaconda2\lib\site-packages\ipykernel_launcher.py:66: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  7%|▋         | 1059/14599 [00:41<08:52, 25.42it/s]

## Guardado de variables

In [ ]:
# Saving the objects:
dir_data = os.path.join(env.data_path, 'reparacion', 'proyecto_inversion', 'var_co_costes_reparacion_02_pi.pkl')

with open(dir_data, 'w') as f:  # Python 3: open(..., 'wb')
    pickle.dump([datos_salida, averia_acum_estado, averia_estado, estado_modos_fallo, origen_maquinaria_reparacion_estado,
                 origen_materiales_reparacion_estado, origen_mano_obra_reparacion_estado,
                 datos_salida_prob_ini_averia], f)

Continuar con [Parte 3 - Representacion de resultados y cálculo de costes.](co_costes_construccion_03_es_c1.ipynb)